In [1]:
import plyvel
import struct
import numpy as np

In [163]:
# functions for reading IAVL tree

def read_varint(x: bytes, offset: int = 0) -> int:
    result = 0
    factor = 1

    for i, b in enumerate(x[offset:]):
        if b >= 128:
            result = result + (b - 128) * factor
        else:
            result = result + b * factor
            return result // 2, offset+i+1
        factor *= 128

def read_uvarint(x: bytes, offset: int = 0) -> int:
    result = 0
    factor = 1

    for i, b in enumerate(x[offset:]):
        if b >= 128:
            result = result + (b - 128) * factor
        else:
            result = result + b * factor
            return result, offset+i+1
        factor *= 128

def read_key(key: bytes) -> tuple[int, int] | None:
    if not key.startswith(b's'):
        return None

    version = struct.unpack_from('>Q', key[1:9])[0]
    nonce = struct.unpack_from('>I', key[9:13])[0]

    return (version, nonce)

def write_key(key: tuple[int, int]) -> bytes:
    version = struct.pack('>Q', key[0])
    nonce = struct.pack('>I', key[1])

    return b's' + version + nonce

def read_node(node: bytes) -> tuple[int, int, bytes, tuple[int, int], tuple[int, int]] | tuple[int, int, list[int], bytes] | tuple[int, int]:

    if node.startswith(b's'):
        return read_key(node)

    n = 0
    height, n = read_varint(node, n)

    if height == 0:
        length, n = read_varint(node, n)
        size, n = read_uvarint(node, n)
        key = node[n:n+size]
        n += size
        valuesize, n = read_uvarint(node, n)
        value = node[n:n+valuesize]

        return (height, length, key, value)
    else:
        length, n = read_varint(node, n)
        size, n = read_uvarint(node, n)
        key = node[n:n+size]
        n += size
        hashsize, n = read_uvarint(node, n)
        n += hashsize
        mode, n = read_uvarint(node, n)
        left_version, n = read_varint(node, n)
        left_nonce, n = read_varint(node, n)
        right_version, n = read_varint(node, n)
        right_nonce, n = read_varint(node, n)

        return (height, length, key, (left_version, left_nonce), (right_version, right_nonce))

def walk(tree, version, searchkey):
    if (version, 1) not in tree:
        return None

    node = tree[(version, 1)]
    if len(node) == 2: # root copy?
        node = tree[node]

    while node[0] > 0:
        nodekey = node[2]
        if searchkey < nodekey:
            next = node[3]
        else:
            next = node[4]

        node = tree[next]

    return node[3]

def walk_disk_raw(db, prefix: bytes, version: int, searchkey: bytes) -> None | bytes:

    root = db.get(prefix + write_key((version, 1)))
    if root is None:
        return None

    node = read_node(root)

    if len(node) == 2: # root copy?
        node = read_node(db.get(prefix + write_key(node)))

    while node[0] > 0:
        # print(node)

        nodekey = node[2]
        if searchkey < nodekey:
            next = node[3]
        else:
            next = node[4]

        node = read_node(db.get(prefix + write_key(next)))

    if node[2] == searchkey:
        return node[3]
    else:
        return None

def walk_disk_next_key_raw(db, prefix: bytes, version: int, searchkey: bytes) -> None | bytes:
    root = db.get(prefix + write_key((version, 1)))
    if root is None:
        return None

    node = read_node(root)
    lowest_geq_key = node[2] if node[2] >= searchkey else None

    if len(node) == 2: # root copy?
        node = read_node(db.get(prefix + write_key(node)))

    while node[0] > 0:
        # print(node)

        nodekey = node[2]
        if searchkey < nodekey:
            next = node[3]
        else:
            next = node[4]

        node = read_node(db.get(prefix + write_key(next)))
        if node[2] >= searchkey and (lowest_geq_key is None or node[2] < lowest_geq_key):
            lowest_geq_key = node[2]

    return lowest_geq_key

def walk_disk(db, prefix: str, version: int, format: str, searchkey: list) -> None | bytes:
    return walk_disk_raw(db, prefix.encode('utf-8'), version, encode_key(format, searchkey))

def parse_struct(data):
    n = 0
    results = []

    while n < len(data):
        key, n = read_uvarint(data, n)
        ty = key & 7
        key >>= 3
        if ty == 2:
            l, n = read_uvarint(data, n)
            val = data[n:n+l]
            n += l
        elif ty == 0:
            val, n = read_uvarint(data, n)
        else:
            raise Exception(f'unknown type {ty}, {data[n:]}')
        results.append((key, val))

    return results

In [54]:
# find max height

def next_key(db, k: bytes) -> bytes | None:
    it = db.iterator(start = k)
    try:
        nk, _ = next(it)
        return nk
    except StopIteration:
        return None
    finally:
        it.close()

def max_height(db) -> int:
    testnr = 1<<63

    for i in range(62, -1, -1):
        prefix = b's/k:emissions/s'
        n = next_key(db, prefix + struct.pack('>Q', testnr))

        if n is not None and n.startswith(prefix):
            # print(f'{testnr:16x} is low')
            testnr += 1 << i
        else:
            # print(f'{testnr:16x} is high')
            testnr -= 1 << i

    n = next_key(db, prefix + struct.pack('>Q', testnr))
    if n is not None and n.startswith(prefix):
        return testnr
    else:
        return testnr - 1

In [176]:
# encode and decode keys

def encode_key(format: str, key: list) -> bytes:
    result_bytes = []

    result_bytes.append(key[0])

    for i, f in enumerate(format):
        if i >= len(key) - 1:
            break
        if f == 's':
            result_bytes += list(key[i+1].encode('utf-8'))
            if i < len(format) - 1:
                result_bytes += [0]
        elif f == 'Q':
            result_bytes += list(struct.pack('>Q', key[i+1]))
        elif f == 'q':
            result_bytes += list(struct.pack('>Q', key[i+1] + (1<<63)))

    return bytes(result_bytes)

def decode_key(format: str, key: bytes) -> list:
    result = []

    result.append(key[0])
    idx = 1

    for f in format:
        if f == 's':
            end = key[idx:].find(b'\x00')
            if end < 0:
                result.append(key[idx:].decode('utf-8'))
                break
            else:
                result.append(key[idx:idx+end].decode('utf-8'))
                idx += end + 1
        elif f == 'Q':
            v = struct.unpack('>Q', key[idx:idx+8])[0]
            result.append(v)
            idx += 8
        elif f == 'q':
            v = struct.unpack('>Q', key[idx:idx+8])[0]
            result.append(v - (1<<63))
            idx += 8

    return result

In [175]:
db = plyvel.DB('nodedir/data/application.db')
height = max_height(db)

In [188]:
# get
v = walk_disk(db, 's/k:emissions/', height, 'Qs', [11, 37, 'allo1mn4d32hwyn6grp89akek52arsw2vcdqezr0dc7'])
parse_struct(v)

[(1, 37),
 (2, 5224812),
 (3, b'allo1mn4d32hwyn6grp89akek52arsw2vcdqezr0dc7'),
 (4, b'183.2449346998165')]

In [3]:
# def has_prefix(db, prefix: bytes) -> bool:
#     it = db.iterator(start = prefix)
#     try:
#         first_key, _ = next(it)
#         return first_key.startswith(prefix)
#     except StopIteration:
#         return False
#     finally:
#         it.close()

# found = []
# prefixes = [b's/']

# for i in range(20):
#     new_prefixes = []

#     for p in prefixes:
#         for i in range(256):
#             b = p + bytes([i])
#             if has_prefix(db, b):
#                 if b.endswith(b'/'):
#                     found.append((b, db.approximate_size(b, b + b'\xff')))
#                 else:
#                     new_prefixes.append(b)
#                 # new_prefixes.append(b)

#     prefixes = new_prefixes

# found